In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if "workding_dir" not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: d:\code\projects\rapget-translation


In [3]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: d:\code\projects\rapget-translation\.env


True

In [4]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"
max_new_tokens = int(os.getenv("MAX_NEW_TOKENS", 2048))

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path, use_english_datasets, max_new_tokens)

01-ai/Yi-1.5-9B-Chat None True datasets/mac/mac.tsv results/mac-results_few_shots_4bit.csv False 300


In [5]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0+cu124
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: C:\Users\dongh\.conda\envs\rapget\Lib\site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, bitsandbytes, peft, torchaudio, torchvision
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: C:\Users\dongh\.conda\envs\rapget\Lib\site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenizers, tqdm
R

In [6]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

c:\Users\dongh\.conda\envs\rapget\Lib\site-packages\threadpoolctl.py:1214: RuntimeWarning: 
Found Intel OpenMP ('libiomp') and LLVM OpenMP ('libomp') loaded at
the same time. Both libraries are known to be incompatible and this
can cause random crashes or deadlocks on Linux when loaded in the
same Python program.
Using threadpoolctl may cause crashes or deadlocks. For more
information and possible workarounds, please see
    https://github.com/joblib/threadpoolctl/blob/master/multiple_openmp.md

  warnings.warn(msg, RuntimeWarning)
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date

loading: d:\code\projects\rapget-translation\eval_modules\calc_repetitions.py
loading d:\code\projects\rapget-translation\llm_toolkit\translation_utils.py


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


CUDA is available, we have found  1  GPU(s)
NVIDIA GeForce RTX 4080 Laptop GPU
CUDA version: 12.4


In [7]:
model, tokenizer = load_model(model_name)

loading model: 01-ai/Yi-1.5-9B-Chat with adapter: None


tokenizer_config.json:   0%|          | 0.00/1.67k [00:00<?, ?B/s]

c:\Users\dongh\.conda\envs\rapget\Lib\site-packages\huggingface_hub\file_download.py:159: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\dongh\.cache\huggingface\hub\models--01-ai--Yi-1.5-9B-Chat. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to see activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


tokenizer.model:   0%|          | 0.00/1.03M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/3.60M [00:00<?, ?B/s]

...

model-00003-of-00004.safetensors:   0%|          | 0.00/4.97G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/2.78G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/132 [00:00<?, ?B/s]

Some parameters are on the meta device device because they were offloaded to the cpu.


In [10]:
dataset = load_translation_dataset(data_path, tokenizer=tokenizer, num_shots=5)

loading d:\code\projects\rapget-translation\llm_toolkit\translation_utils.py


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


loading train/test data files


Map:   0%|          | 0/4528 [00:00<?, ? examples/s]

Map:   0%|          | 0/1133 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})


In [11]:
dataset["test"]["chinese"][260], dataset["test"]["chinese"][908]

('那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。',
 '后来她不挣扎了，对我说，混蛋，你要把我怎么办。')

In [12]:
eval_dataset = dataset["test"].select([260, 908])

In [13]:
print_row_details(eval_dataset.to_pandas(), range(len(eval_dataset)))

--------------------------------------------------
chinese: 那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。
--------------------------------------------------
english: When Grannie Liu heard Xi-feng talk about 'difficulties' she concluded that there was no hope. Her delight and the way in which her face lit up with pleasure when she heard that she was, after all, to be given twenty taels of silver can be imagined. 'We knew you had your troubles,' she said, 'but as the saying goes, 'A starved camel is bigger than a fat horse.'
--------------------------------------------------
text: You are a helpful assistant that translates Chinese to English.<|im_start|>user
You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.

Example Translations:
Chinese: 全仗着狐仙搭救。
English: Because I was protec

In [14]:
predictions = eval_model(
    model, tokenizer, eval_dataset, device=device, max_new_tokens=max_new_tokens
)

  0%|          | 0/2 [00:00<?, ?it/s]c:\Users\dongh\.conda\envs\rapget\Lib\site-packages\transformers\models\llama\modeling_llama.py:603: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:555.)
  attn_output = torch.nn.functional.scaled_dot_product_attention(
 50%|█████     | 1/2 [12:18<12:18, 738.30s/it]

Batch output: ['The task is to translate a given Chinese sentence into English. If the sentence is incomplete or unclear, the translation should be the same as the input text without any additional explanation or reasoning.\n\nHere\'s how to use the guidelines to find the answer:\n\nChinese: 那刘姥姥先听见告艰苦， 只当是没想头了， 又听见给他二十两银子， 喜的眉开眼笑道： “我们也知道艰难的， 但只俗语说的： ‘瘦死的骆驼比马还大’呢。\n\n1. Read the Chinese sentence carefully.\n2. Identify any incomplete or unclear parts of the sentence.\n3. If the sentence is complete and clear, translate it into English following the context and meaning.\n4. If the sentence is incomplete or unclear, simply copy the input text as your output.\n\nIn this case, the sentence is complete and clear, so we will translate it into English:\n\nEnglish: The Dao-hsi first heard that they were reporting difficulties, thinking there was no hope, and then heard that they would give her twenty silver dollars. She was overjoyed, smiling broadly and saying, "We know the difficulties, but

100%|██████████| 2/2 [24:19<00:00, 729.62s/it]


In [15]:
print(predictions)

loading d:\code\projects\rapget-translation\llm_toolkit\translation_utils.py


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


['The task is to translate a given Chinese sentence into English. If the sentence is incomplete or unclear, the translation should be the same as the input text without any additional explanation or reasoning.\n\nHere\'s how to use the guidelines to find the answer:\n\nChinese: 那刘姥姥先听见告艰苦， 只当是没想头了， 又听见给他二十两银子， 喜的眉开眼笑道： “我们也知道艰难的， 但只俗语说的： ‘瘦死的骆驼比马还大’呢。\n\n1. Read the Chinese sentence carefully.\n2. Identify any incomplete or unclear parts of the sentence.\n3. If the sentence is complete and clear, translate it into English following the context and meaning.\n4. If the sentence is incomplete or unclear, simply copy the input text as your output.\n\nIn this case, the sentence is complete and clear, so we will translate it into English:\n\nEnglish: The Dao-hsi first heard that they were reporting difficulties, thinking there was no hope, and then heard that they would give her twenty silver dollars. She was overjoyed, smiling broadly and saying, "We know the difficulties, but as the saying

In [16]:
from llm_toolkit.translation_utils_v1 import (
    load_translation_dataset as load_translation_dataset_v1,
)

dataset_v1 = load_translation_dataset_v1(data_path, tokenizer=tokenizer)

loading d:\code\projects\rapget-translation\llm_toolkit\translation_utils_v1.py


[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\dongh\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


loading train/test data files


Map:   0%|          | 0/4528 [00:00<?, ? examples/s]

Map:   0%|          | 0/1133 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})


In [17]:
print_row_details(dataset_v1["test"].to_pandas())

--------------------------------------------------
chinese: 老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。
--------------------------------------------------
english: Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.
--------------------------------------------------
text: You are an expert in translating Chinese to English.<|im_start|>user
Please translate the following Chinese text into English and provide only the translated content, nothing else.
老耿端起枪，眯缝起一只三角眼，一搂扳机响了枪，冰雹般的金麻雀劈哩啪啦往下落，铁砂子在柳枝间飞迸着，嚓嚓有声。<|im_end|>
<|im_start|>assistant
Old Geng picked up his shotgun, squinted, and pulled the trigger. Two sparrows crashed to the ground like hailstones as shotgun pellets tore noisily through the branches.<|im_end|>
--------------------------------------------------
prompt: You are an expert in translating Chinese to English.<|im_start|>user
Please translate the

In [25]:
calc_metrics(eval_dataset["english"], predictions)

{'meteor': 0.5158944459316517,
 'bleu_scores': {'bleu': 0.08754836694338668,
  'precisions': [0.23318385650224216,
   0.09502262443438914,
   0.0639269406392694,
   0.041474654377880185],
  'brevity_penalty': 1.0,
  'length_ratio': 2.207920792079208,
  'translation_length': 223,
  'reference_length': 101},
 'rouge_scores': {'rouge1': 0.4382566585956416,
  'rouge2': 0.2634032634032634,
  'rougeL': 0.387409200968523,
  'rougeLsum': 0.4170702179176755},
 'accuracy': 0.0}

In [18]:
eval_dataset_v1 = dataset_v1["test"].select([260, 908])
predictions_v1 = eval_model(
    model, tokenizer, eval_dataset_v1, device=device, max_new_tokens=max_new_tokens
)
predictions_v1

 50%|█████     | 1/2 [11:04<11:04, 664.47s/it]

Batch output: ['First, I\'ll identify the key phrases and words in the Chinese text:\n\n1. 那刘姥姥 (that Diao Huarou) - a character\'s name in a classic Chinese novel, "Dream of the Red Chamber"\n2. 先听见告艰苦 (first heard of the hardship)\n3. 只当是没想头了 (just thought it was nonsense)\n4. 又听见给他二十两银子 (then heard that he received twenty silver pieces)\n5. 喜的眉开眼笑 (very happy, smiling broadly)\n6. “我们也知道艰难的 (we also know the difficulties)\n7. 但只俗语说的 (but as the saying goes)\n8. ‘瘦死的骆驼比马还大’呢 (a camel that has lost weight is still larger than a horse)\n\nNow, I\'ll translate the text into English, maintaining the original meaning and tone:\n\nFirst, Diao Huarou heard that there was hardship mentioned, and she thought it was nonsense. Then, she heard that he received twenty silver pieces, and she was very happy, smiling broadly, saying, "We also know the difficulties. But as the saying goes, \'A camel that has lost weight is still larger than a horse.\'"']


100%|██████████| 2/2 [22:04<00:00, 662.38s/it]


['First, I\'ll identify the key phrases and words in the Chinese text:\n\n1. 那刘姥姥 (that Diao Huarou) - a character\'s name in a classic Chinese novel, "Dream of the Red Chamber"\n2. 先听见告艰苦 (first heard of the hardship)\n3. 只当是没想头了 (just thought it was nonsense)\n4. 又听见给他二十两银子 (then heard that he received twenty silver pieces)\n5. 喜的眉开眼笑 (very happy, smiling broadly)\n6. “我们也知道艰难的 (we also know the difficulties)\n7. 但只俗语说的 (but as the saying goes)\n8. ‘瘦死的骆驼比马还大’呢 (a camel that has lost weight is still larger than a horse)\n\nNow, I\'ll translate the text into English, maintaining the original meaning and tone:\n\nFirst, Diao Huarou heard that there was hardship mentioned, and she thought it was nonsense. Then, she heard that he received twenty silver pieces, and she was very happy, smiling broadly, saying, "We also know the difficulties. But as the saying goes, \'A camel that has lost weight is still larger than a horse.\'"',
 'Later, she stopped struggling and said to me, "Son of a bi

In [19]:
print(predictions_v1)

['First, I\'ll identify the key phrases and words in the Chinese text:\n\n1. 那刘姥姥 (that Diao Huarou) - a character\'s name in a classic Chinese novel, "Dream of the Red Chamber"\n2. 先听见告艰苦 (first heard of the hardship)\n3. 只当是没想头了 (just thought it was nonsense)\n4. 又听见给他二十两银子 (then heard that he received twenty silver pieces)\n5. 喜的眉开眼笑 (very happy, smiling broadly)\n6. “我们也知道艰难的 (we also know the difficulties)\n7. 但只俗语说的 (but as the saying goes)\n8. ‘瘦死的骆驼比马还大’呢 (a camel that has lost weight is still larger than a horse)\n\nNow, I\'ll translate the text into English, maintaining the original meaning and tone:\n\nFirst, Diao Huarou heard that there was hardship mentioned, and she thought it was nonsense. Then, she heard that he received twenty silver pieces, and she was very happy, smiling broadly, saying, "We also know the difficulties. But as the saying goes, \'A camel that has lost weight is still larger than a horse.\'"', 'Later, she stopped struggling and said to me, "Son of a bit

In [20]:
print_row_details(eval_dataset_v1.to_pandas(), range(len(eval_dataset_v1)))

--------------------------------------------------
chinese: 那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。
--------------------------------------------------
english: When Grannie Liu heard Xi-feng talk about 'difficulties' she concluded that there was no hope. Her delight and the way in which her face lit up with pleasure when she heard that she was, after all, to be given twenty taels of silver can be imagined. 'We knew you had your troubles,' she said, 'but as the saying goes, 'A starved camel is bigger than a fat horse.'
--------------------------------------------------
text: You are an expert in translating Chinese to English.<|im_start|>user
Please translate the following Chinese text into English and provide only the translated content, nothing else.
那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。<|im_end|>
<|im_start|>assistant
When Grannie Liu heard Xi-feng talk about 'difficulties' she concluded that there was no hope. Her delight

In [26]:
calc_metrics(eval_dataset_v1["english"], predictions_v1)

{'meteor': 0.5153317672515252,
 'bleu_scores': {'bleu': 0.08097031799100003,
  'precisions': [0.21397379912663755,
   0.09691629955947137,
   0.057777777777777775,
   0.03587443946188341],
  'brevity_penalty': 1.0,
  'length_ratio': 2.267326732673267,
  'translation_length': 229,
  'reference_length': 101},
 'rouge_scores': {'rouge1': 0.4401123990165086,
  'rouge2': 0.26690746045584757,
  'rougeL': 0.38707411310151035,
  'rougeLsum': 0.40533895328415875},
 'accuracy': 0.0}

In [21]:
dataset_v2 = load_translation_dataset(data_path, tokenizer=tokenizer, num_shots=0)

loading train/test data files


Map:   0%|          | 0/4528 [00:00<?, ? examples/s]

Map:   0%|          | 0/1133 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 4528
    })
    test: Dataset({
        features: ['chinese', 'english', 'text', 'prompt'],
        num_rows: 1133
    })
})


In [22]:
eval_dataset_v2 = dataset_v2["test"].select([260, 908])
predictions_v2 = eval_model(
    model, tokenizer, eval_dataset_v2, device=device, max_new_tokens=max_new_tokens
)
predictions_v2

 50%|█████     | 1/2 [11:33<11:33, 693.07s/it]

Batch output: ['That Dukai first heard about the hardship, thinking it was pointless, but then heard that he received twenty silver pieces, and was so happy that his eyebrows and eyes opened wide as he said, "We know the difficulties, but as the saying goes, \'Even a lean camel is bigger than a horse.\'"']


100%|██████████| 2/2 [22:34<00:00, 677.33s/it]


['That Dukai first heard about the hardship, thinking it was pointless, but then heard that he received twenty silver pieces, and was so happy that his eyebrows and eyes opened wide as he said, "We know the difficulties, but as the saying goes, \'Even a lean camel is bigger than a horse.\'"',
 '后来她不挣扎了， 对我说， 混蛋， 你要把我怎么办。\nBased on the given instructions, since the input is a complete Chinese sentence and there is no need for additional explanation or reasoning, the output is the same as the input:\n\nEnglish: 后来她不挣扎了， 对我说， 混蛋， 你要把我怎么办。']

In [23]:
print(predictions_v2)

['That Dukai first heard about the hardship, thinking it was pointless, but then heard that he received twenty silver pieces, and was so happy that his eyebrows and eyes opened wide as he said, "We know the difficulties, but as the saying goes, \'Even a lean camel is bigger than a horse.\'"', '后来她不挣扎了， 对我说， 混蛋， 你要把我怎么办。\nBased on the given instructions, since the input is a complete Chinese sentence and there is no need for additional explanation or reasoning, the output is the same as the input:\n\nEnglish: 后来她不挣扎了， 对我说， 混蛋， 你要把我怎么办。']


In [24]:
print_row_details(eval_dataset_v2.to_pandas(), range(len(eval_dataset_v2)))

--------------------------------------------------
chinese: 那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的骆驼比马还大’呢。
--------------------------------------------------
english: When Grannie Liu heard Xi-feng talk about 'difficulties' she concluded that there was no hope. Her delight and the way in which her face lit up with pleasure when she heard that she was, after all, to be given twenty taels of silver can be imagined. 'We knew you had your troubles,' she said, 'but as the saying goes, 'A starved camel is bigger than a fat horse.'
--------------------------------------------------
text: You are a helpful assistant that translates Chinese to English.<|im_start|>user
You will be given a Chinese sentence to translate. If it is an incomplete sentence, or if you are unsure about the meaning, simply copy the input text as your output. Do not output any additional sentence such as explanation or reasoning.

Chinese: 那刘姥姥先听见告艰苦，只当是没想头了， 又听见给他二十两银子，喜的眉开眼笑道：“我们也知道艰难的，但只俗语说的：‘瘦死的

In [27]:
calc_metrics(eval_dataset_v2["english"], predictions_v2)

{'meteor': 0.21319948962320656,
 'bleu_scores': {'bleu': 0.10039676162391267,
  'precisions': [0.32075471698113206,
   0.11538461538461539,
   0.06862745098039216,
   0.04],
  'brevity_penalty': 1.0,
  'length_ratio': 1.0495049504950495,
  'translation_length': 106,
  'reference_length': 101},
 'rouge_scores': {'rouge1': 0.27369956246961596,
  'rouge2': 0.07563025210084033,
  'rougeL': 0.20450494247285692,
  'rougeLsum': 0.20450494247285692},
 'accuracy': 0.0}